# Introduction to Dynamics

Joe(y) Carpinelli  
2021-07-04

## Overview

Our end goal as controls engineers is to *affect* a system in some
desired way. To do this, we’ll need a mathematical description of our
system. This mathematical description is known as a *model*. There’s a
famous [quote](https://en.wikipedia.org/wiki/All_models_are_wrong) about
mathematical models: “all models are wrong, but some are useful”.

This is really important. We are **always** approximating our system by
describing it with a model. The question we need to ask is “is our
approximate description of our system (our model) good enough?”

> **Definitions**
>
> -   **Model**: a mathematical description of a system

But what does this model *look like*? To answer this question, let’s
first discuss system dynamics, and equations of motion.

## Dynamics

If we want to *affect* a system, then by definition, the system *should*
be affect-able (is that a word?) by external forces. These “forces”
don’t necessarily need to be physical forces: consider the affect of
introducing new predators in an ecosystem with the goal of affecting
predator-prey populations.

So we have a mathematical description, and we know we’ll need some
changing *parameter* to affect the mathematical description. Sounds like
we need equations! The equations that govern our system are often called
*equations of motion*. Any system that changes due to some external
“force” is known as a *dynamical* system by definition.

The first step to any controls problem is identifying the *dynamics*;
this usually means defining the *equations of motion* for our system. A
set of *equations of motion* which describe our *dynamical* system
**is** our model.

## Example

A really common system in engineering is known as the
**spring-mass-damper**. We can roughly describe this system as a block
on a table, which is connected to a spring. We can *force* (a.k.a.
*affect*) this system by pulling on the block to extend or compress the
spring.

### Model Construction

Let’s figure out our equations of motion. The following question is
usually a useful starting point: “what are the forces on our system?” We
know we’ll have one external force: us pulling or pushing on the block!
Let’s call this external force $f_e$. We’ll also have a force due to the
spring, and a force due to the friction between the block and the table.
The force due to the spring will be *proportional* to the position of
the block with respect to the spring’s neutral position: let’s call the
spring constant $k$. The force due to friction will be proportional to
the *velocity* of the block (let’s forget about static friction for
now): let’s call the coefficient of friction $d$.

With all of the forces identified, we can start constructing the
*equations of motion* for this system. If we call our block’s position
$x$, then the acceleration $\ddot{x}$ will be equal to the sum of our
external force $f_e$, the spring force $k x$, and the force due to
friction $d \dot{x}$. Summing these forces produces the following
(common) spring-mass-damper equation, where $m$ is the mass of the
block.

<span id="eq-forced-mass-damper">$$
f_e = m \ddot{x} + d \dot{x} + k x
 \qquad(1)$$</span>

We have our model! This is a second-order differential equation
(<a href="#eq-forced-mass-damper" class="quarto-xref">Equation 1</a>).
It helps to divide all variables into two groups: parameters, and
states. States describe the system at some point in time. In this case,
state variables answer the following questions: “where is the block,
what is the velocity of the block, and what is the acceleration of the
block?” One set of valid state variables for this system is $x$ and
$\dot{x}$; we don’t need to include $\ddot{x}$ in our list of state
variables because we can calculate $\ddot{x}$ from $x$ and $\dot{x}$.

> **Note**
>
> We say “one set of state variables” because there may (and nearly
> always are) other valid state representations that could completely
> describe this system! State variables are **not** unique.

If we leave states as symbolic, and then look to the equation(s) of
motion of a system, the *parameters* describe a specific *instance* of a
system. Put another way, no matter what values $f_e$, $d$, and $k$ take,
this equation of motion is identifiable as a spring-mass-damper. For
this reason, we can specify $f_e$, $d$, and $k$ as parameters. We can
assume a unit mass for the block for now.

> **Note**
>
> The parameter $f_e$ is our *control* parameter in this example,
> because we can change $f_e$ to affect our system. For now, let’s not
> differentiate between control parameters and non-control parameters.

### Coding our Model

We can simulate these dynamics with Julia’s `DifferentialEquations`
package. If you’re familiar with MATLAB, `DifferentialEquations`
provides numerical integration solvers that are similar to MATLAB’s
`ode45` (and similar) solvers. We can use the `ModelingToolkit` package
to conveniently put our model to code, and interface with
`DifferentialEquations` for simulation.

In [1]:
using ModelingToolkit, DifferentialEquations, Plots

Now that we have access to `ModelingToolkit`, let’s build the model!

In [1]:
@parameters t fₑ d k
@variables x(t) ẋ(t)
δ = Differential(t)

eqs = [
    δ(x) ~ ẋ,
    δ(ẋ) ~ -d * ẋ - k * x + fₑ
]

model = complete(
    ODESystem(eqs, t, [x, ẋ], [fₑ, d, k]; name=:HarmonicOscillator)
)

Model HarmonicOscillator with 2 equations 
 States (2): 
 x(t)
 ẋ(t)
 Parameters (3): 
 fₑ
 d
 k

### Simulating our Model

With `model` defined above, we can use `DifferentialEquations` to
simulate our system. Of course, to do this we’ll need to specify
numerical values for our parameters, and initial conditions (the
simulation starting point) for our state variables. The code below
specifies some arbitrary initial conditions and constant parameter
values, and simulates the resulting dynamics.

In [1]:
problem = let x₀ = 0.1, ẋ₀ = 0.0, dₙ = 0.5, kₙ = 0.9, fₙ = 1.0, Δt = 30.0
    ODEProblem(
        model,
        [x => x₀, ẋ => ẋ₀],
        (0.0, Δt),
        [d => dₙ, k => kₙ, fₑ => fₙ]
    )
end

solutions = solve(problem, Tsit5(); reltol=1e-12, abstol=1e-12)
plot(solutions; linewidth=2, dpi=130, title="Spring Mass Damper Simulation")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip510)" d="M158.992 1767.34 Q155.381 1767.34 153.552 1770.9 Q151.747 1774.45 151.747 1781.58 Q151.747 1788.68 153.552 1792.25 Q155.381 1795.79 158.992 1795.79 Q162.626 1795.79 164.432 1792.25 Q166.261 1788.68 166.261 1781.58 Q166.261 1774.45 164.432 1770.9 Q162.626 1767.34 158.992 1767.34 M158.992 1763.64 Q164.802 1763.64 167.858 1768.24 Q170.937 1772.83 170.937 1781.58 Q170.937 1790.3 167.858 1794.91 Q164.802 1799.49 158.992 1799.49 Q153.182 1799.49 150.103 1794.91 Q147.048 1790.3 147.048 1781.58 Q147.048 1772.83 150.103 1768.24 Q153.182 1763.64 158.992 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip510)" d="M1000.29 1767.34 Q996.675 1767.34 994.846 1770.9 Q993.041 1774.45 993.041 1781.58 Q993.041 1788.68 994.846 1792.25 Q996.675 1795.79 1000.29 1795.79 Q1003.92 1795.79 1005.73 1792.25 Q1007.55 1788.68 1007.55 1781.58 Q1007.55 1774.45 1005.73 1770.9 Q1003.92 1767.34 1000.29 1767.34 M1000.29 1763.64 Q1006.1 1763.64 1009.15 1768.24 Q1012.23 1772.83 1012.23 1781.58 Q1012.23 1790.3 1009.15 1794.91 Q1006.1 1799.49 1000.29 1799.49 Q994.476 1799.49 991.397 1794.91 Q988.342 1790.3 988.342 1781.58 Q988.342 1772.83 991.397 1768.24 Q994.476 1763.64 1000.29 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip510)" d="M1792.27 1794.89 L1808.59 1794.89 L1808.59 1798.82 L1786.65 1798.82 L1786.65 1794.89 Q1789.31 1792.13 1793.89 1787.5 Q1798.5 1782.85 1799.68 1781.51 Q1801.93 1778.98 1802.81 1777.25 Q1803.71 1775.49 1803.71 1773.8 Q1803.71 1771.04 1801.77 1769.31 Q1799.84 1767.57 1796.74 1767.57 Q1794.54 1767.57 1792.09 1768.34 Q1789.66 1769.1 1786.88 1770.65 L1786.88 1765.93 Q1789.71 1764.79 1792.16 1764.21 Q1794.61 1763.64 1796.65 1763.64 Q1802.02 1763.64 1805.21 1766.32 Q1808.41 1769.01 1808.41 1773.5 Q1808.41 1775.63 1807.6 1777.55 Q1806.81 1779.45 1804.71 1782.04 Q1804.13 1782.71 1801.02 1785.93 Q1797.92 1789.12 1792.27 1794.89 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip510)" d="M1828.41 1767.34 Q1824.8 1767.34 1822.97 1770.9 Q1821.16 1774.45 1821.16 1781.58 Q1821.16 1788.68 1822.97 1792.25 Q1824.8 1795.79 1828.41 1795.79 Q1832.04 1795.79 1833.85 1792.25 Q1835.68 1788.68 1835.68 1781.58 Q1835.68 1774.45 1833.85 1770.9 Q1832.04 1767.34 1828.41 1767.34 M1828.41 1763.64 Q1834.22 1763.64 1837.27 1768.24 Q1840.35 1772.83 1840.35 1781.58 Q1840.35 1790.3 1837.27 1794.91 Q1834.22 1799.49 1828.41 1799.49 Q1822.6 1799.49 1819.52 1794.91 Q1816.46 1790.3 1816.46 1781.58 Q1816.46 1772.83 1819.52 1768.24 Q1822.6 1763.64 1828.41 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip510)" d="M2629.6 1780.19 Q2632.96 1780.9 2634.83 1783.17 Q2636.73 1785.44 2636.73 1788.77 Q2636.73 1793.89 2633.21 1796.69 Q2629.69 1799.49 2623.21 1799.49 Q2621.03 1799.49 2618.72 1799.05 Q2616.43 1798.64 2613.97 1797.78 L2613.97 1793.27 Q2615.92 1794.4 2618.23 1794.98 Q2620.55 1795.56 2623.07 1795.56 Q2627.47 1795.56 2629.76 1793.82 Q2632.08 1792.08 2632.08 1788.77 Q2632.08 1785.72 2629.92 1784.01 Q2627.79 1782.27 2623.97 1782.27 L2619.95 1782.27 L2619.95 1778.43 L2624.16 1778.43 Q2627.61 1778.43 2629.44 1777.06 Q2631.27 1775.67 2631.27 1773.08 Q2631.27 1770.42 2629.37 1769.01 Q2627.49 1767.57 2623.97 1767.57 Q2622.05 1767.57 2619.85 1767.99 Q2617.65 1768.4 2615.02 1769.28 L2615.02 1765.12 Q2617.68 1764.38 2619.99 1764.01 Q2622.33 1763.64 2624.39 1763.64 Q2629.71 1763.64 2632.82 1766.07 Q2635.92 1768.47 2635.92 1772.59 Q2635.92 1775.46 2634.27 1777.46 Q2632.63 1779.42 2629.6 1780.19 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip510)" d="M2655.59 1767.34 Q2651.98 1767.34 2650.15 1770.9 Q2648.35 1774.45 2648.35 1781.58 Q2648.35 1788.68 2650.15 1792.25 Q2651.98 1795.79 2655.59 1795.79 Q2659.23 1795.79 2661.03 1792.25 Q2662.86 1788.68 2662.86 1781.58 Q2662.86